# Użytkownicy, których lokację znamy

## Wczytywanie danych

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
data_folder = '/content/drive/MyDrive/Przestrzenne, zaliczenie/data'

In [3]:
import pickle
import os

locations_cache_path = os.path.join(data_folder, 'locations_geocoded.pkl')
locations_cache = pickle.load(open(locations_cache_path, 'rb+'))

In [4]:
type(locations_cache), list(locations_cache)[45:50]

(dict,
 ['Warszawa, Polska',
  'Piwo ',
  'Toruń, Gdynia, Kraków, Poznań ',
  'Barczewo',
  'Gliwice, Polska'])

## Przygotowanie środowiska

In [5]:
############## Poradnik dla opornych
## Do instalacji GDAL - https://www.lfd.uci.edu/~gohlke/pythonlibs/#gdal
!pip install GDAL-3.4.1-pp38-pypy38_pp73-win_amd64.whl
## Do instalacji bibliotekę Fiona (https://www.lfd.uci.edu/~gohlke/pythonlibs/#fiona) (tutorial: https://stackoverflow.com/questions/50876702/cant-install-fiona-on-windows)
!pip install <path/to/Fiona.whl>
!pip install geopandas

ERROR: GDAL-3.4.1-pp38-pypy38_pp73-win_amd64.whl is not a supported wheel on this platform.
/bin/bash: -c: line 0: syntax error near unexpected token `newline'
/bin/bash: -c: line 0: `pip install <path/to/Fiona.whl>'


In [6]:
!pip install folium

## Czyszczenie danych

In [7]:
print(f'Wszystkich zebranych z API geocodeów jest {len(locations_cache)}')
not_nones = dict([(code, loc) for code, loc in locations_cache.items() if loc is not None])
not_nones.pop(None, None)
print(f'Geocodeów, którym API przypisało jakiekolwiek miejsce na Ziemi (nie są nullami) jest {len(not_nones)}')

in_poland_counter = 0
only_poland_counter = 0
voivodeship_counter = 0
polish_geocodes = dict()
for geocode, location in not_nones.items():
  if location is not None and 'Polska' in location.address:
    in_poland_counter+=1
    if 'Polska' == location.address:
      only_poland_counter+=1
    if 'województwo' in location.address:
      voivodeship_counter+=1
      polish_geocodes[geocode] = location
print(f'Spośród tych, {in_poland_counter} jest w Polsce')
print(f'A z kolei wśród tych jest {voivodeship_counter} z przypisanym województwem')
print(f'A {only_poland_counter} ma w geocodzie tylko słowo "Polska".')

Wszystkich zebranych z API geocodeów jest 2301
Geocodeów, którym API przypisało jakiekolwiek miejsce na Ziemi (nie są nullami) jest 1592
Spośród tych, 1073 jest w Polsce
A z kolei wśród tych jest 1030 z przypisanym województwem
A 42 ma w geocodzie tylko słowo "Polska".


In [8]:
for location in list(polish_geocodes.values())[50:55]:
  if location and 'Polska' in location.address:
    print(location)

Beskidy, Sidzina, gmina Bystra-Sidzina, powiat suski, województwo małopolskie, 34-236, Polska
Górny Śląsk, Adelina, gmina Werbkowice, powiat hrubieszowski, województwo lubelskie, 22-546, Polska
5, Sądowa, Stare Miasto, Świecie, gmina Świecie, powiat świecki, województwo kujawsko-pomorskie, 86-100, Polska
Stary Sącz, gmina Stary Sącz, powiat nowosądecki, województwo małopolskie, 33-340, Polska
UAM Kampus, Uniwersytetu Poznańskiego, Morasko, Morasko-Radojewo, Poznań, województwo wielkopolskie, 60-687, Polska


In [9]:
locs_per_voivodeship = dict()
for code, location in polish_geocodes.items():
  voiv_name = location.address.split('województwo')[1].split(',')[0].strip()
  locs_per_voivodeship[voiv_name] = locs_per_voivodeship.get(voiv_name, 0) + 1
locs_per_voivodeship

{'dolnośląskie': 81,
 'kujawsko-pomorskie': 47,
 'lubelskie': 58,
 'lubuskie': 21,
 'mazowieckie': 216,
 'małopolskie': 94,
 'opolskie': 19,
 'podkarpackie': 42,
 'podlaskie': 21,
 'pomorskie': 70,
 'warmińsko-mazurskie': 34,
 'wielkopolskie': 82,
 'zachodniopomorskie': 41,
 'łódzkie': 65,
 'śląskie': 116,
 'świętokrzyskie': 23}

In [10]:
# from geopy.geocoders import Nominatim

# geolocator = Nominatim(timeout=10, user_agent = "vaccination_data")

# voivodeship_locations = dict()
# for voiv_name, _ in locs_per_voivodeship.items():
#   if voiv_name not in voivodeship_locations:
#     location = geolocator.geocode(f'{voiv_name}, Polska')
#     voivodeship_locations[voiv_name] = location
# pickle.dump(voivodeship_locations, open(os.path.join(data_folder, 'voivodeship_locations.pkl'), 'wb+'))

In [11]:
voivodeship_locations = pickle.load(open(os.path.join(data_folder, 'voivodeship_locations.pkl'), 'rb+'))
voivodeship_locations

{'dolnośląskie': Location(województwo dolnośląskie, Polska, (50.95083795, 16.36124870197179, 0.0)),
 'kujawsko-pomorskie': Location(województwo kujawsko-pomorskie, Polska, (53.3220016, 18.3392939, 0.0)),
 'lubelskie': Location(województwo lubelskie, Polska, (50.8586338, 22.7732404, 0.0)),
 'lubuskie': Location(województwo lubuskie, Polska, (52.1001754, 15.3605075, 0.0)),
 'mazowieckie': Location(województwo mazowieckie, Polska, (52.5461934, 21.2073404, 0.0)),
 'małopolskie': Location(województwo małopolskie, Polska, (49.790952, 20.3793521, 0.0)),
 'opolskie': Location(województwo opolskie, Polska, (50.8918612, 17.9321175, 0.0)),
 'podkarpackie': Location(województwo podkarpackie, Polska, (49.9927121, 22.177107, 0.0)),
 'podlaskie': Location(województwo podlaskie, Polska, (53.2668455, 22.8525787, 0.0)),
 'pomorskie': Location(województwo pomorskie, Polska, (54.24556, 18.1099, 0.0)),
 'warmińsko-mazurskie': Location(województwo warmińsko-mazurskie, Polska, (53.9311892, 21.1260808, 0.0)),

## Prezentacja

In [12]:
import folium 
from folium import plugins
from geopy.geocoders import Nominatim

geolocator = Nominatim(timeout=10, user_agent = "vaccination_data")
Polska = geolocator.geocode('Poland')
map = folium.Map(location=[Polska.latitude,Polska.longitude],
                    width="%100",height="%100",
                    zoom_start=8)

In [13]:
for code, location in polish_geocodes.items():
  folium.Marker(location=[location.latitude,location.longitude], popup=code).add_to(map)

# minimap = plugins.MiniMap()
# map.add_child(minimap)
map


In [14]:
map_2 = folium.Map(location=[Polska.latitude,Polska.longitude],
                    width="%100",height="%100",
                    zoom_start=8)
for voiv_name, location in voivodeship_locations.items():
  folium.Marker(location=[location.latitude,location.longitude], popup=voiv_name).add_to(map_2)

# minimap = plugins.MiniMap()
# map.add_child(minimap)
map_2

# JOIN między tymi użytkownikami, a Tweetami z info. o nastawieniu

## Wczytywanie danych

In [21]:
tweet_user_location_path = os.path.join(data_folder, 'tweets_labeled_reduced_join_locations.pkl')
tweet_user_location = pickle.load(open(os.path.join(data_folder, 'tweets_labeled_reduced_join_locations.pkl'), 'rb+'))
tweet_user_location[0], len(tweet_user_location)

({'location_by_API': Location(województwo wielkopolskie, Polska, (52.1458506, 17.397672, 0.0)),
  'location_by_user': 'Wielkopolskie, Polska',
  'user_id': 837675106285551618,
  'y2classes_numeric': -1,
  'y3classes_numeric': 0},
 9117)

## Czyszczenie danych

In [25]:
polish_geocodes_set =  set(polish_geocodes.keys())
polish_tweets_data = []
for row in tweet_user_location:
  location_by_user = row['location_by_user']
  if location_by_user in polish_geocodes_set:
    polish_tweets_data.append(row)
print(f'Uzyskano {len(polish_tweets_data)} różnych rodzajów tweetów w Polsce')

Uzyskano 3554 różnych rodzajów tweetów w Polsce


In [41]:
map_y2 = folium.Map(location=[Polska.latitude,Polska.longitude],
                  width="%100",height="%100",
                  zoom_start=8)
for row in polish_tweets_data:
  if row['y2classes_numeric'] == -1:
    color = 'red'
  elif row['y2classes_numeric'] == 0:
    color = 'blue'
  elif row['y2classes_numeric'] == 1:
    color = 'green'
  user_id = row['user_id']
  location = row['location_by_API']
  folium.Marker(location=[location.latitude, location.longitude], 
                popup=folium.Popup(user_id), 
                icon=folium.Icon(color=color))\
      .add_to(map_y2)    
map_y2

In [40]:
map_y3 = folium.Map(location=[Polska.latitude,Polska.longitude],
                  width="%100",height="%100",
                  zoom_start=8)
for row in polish_tweets_data:
  if row['y3classes_numeric'] == -1:
    color = 'red'
  elif row['y3classes_numeric'] == 0:
    color = 'blue'
  elif row['y3classes_numeric'] == 1:
    color = 'green'
  user_id = row['user_id']
  location = row['location_by_API']
  folium.Marker(location=[location.latitude, location.longitude], 
                popup=folium.Popup(user_id), 
                icon=folium.Icon(color=color))\
      .add_to(map_y3)    
map_y3

Output hidden; open in https://colab.research.google.com to view.